In [13]:
import glob
import json
import more_itertools
import numpy as np

In [195]:
! pip install more_itertools

In [6]:
len(glob.glob("*.json"))

1024

In [51]:
def get_irm_score(result_dict):
    '''
    '''
    #Correcting the classifier if the labeeling is learnt is reverse manner
    for curr_cat in result_dict["data_args"]["cat_list"]:
        optimal_vacc = result_dict["ood_vacc"][curr_cat][curr_cat]
        #Flip the labels if we are getting the wrong labels (this shouldn't have happened)
        if(optimal_vacc<0.5):
            for oth_cat in result_dict["data_args"]["cat_list"]:
                result_dict["ood_vacc"][curr_cat][oth_cat]= 1-result_dict["ood_vacc"][curr_cat][oth_cat]
        
        
    
    #Iterating overall the domains
#     print("Getting spurousness score for:{}".format(result_dict["alive_feature_dims"]))
    all_perf_drop = []
    for curr_cat in result_dict["data_args"]["cat_list"]:
        optimal_vacc = result_dict["ood_vacc"][curr_cat][curr_cat]
        
            
        #how the current classifier is different from the otherdomains
        for oth_cat in result_dict["data_args"]["cat_list"]:
            if(curr_cat==oth_cat):
                continue
            
            #Now get the performance of this domain on other optimal classifier
            other_vacc = result_dict["ood_vacc"][oth_cat][curr_cat]
            perf_drop = other_vacc - optimal_vacc
            all_perf_drop.append(perf_drop)
            
#             if(perf_drop>0):
#                 print("Perf Better than optimal perf:\tcurr:{}\tother:{}\tdrop:{}".format(curr_cat,oth_cat,perf_drop))
    
    return np.mean(np.abs(all_perf_drop))
            
        

def read_all_result_file():
    all_result_dict={}
    for res_file in glob.glob("*.json"):
        with open(res_file,"r") as rhandle:
            res_dict = json.load(rhandle)
            #Adding the new spuriousness scrore
            irm_score = get_irm_score(res_dict)
            res_dict["ood_meta_dict"]["irm_score"]=irm_score
            
            all_result_dict[tuple(res_dict["alive_feature_dims"])] = res_dict
    
    return all_result_dict


In [150]:
import numpy as np
np.random.seed(22)
from scipy.special import softmax
    
def spurious_by_em(all_result_dict,num_epochs):
    init_temp=1000.0
    num_feat = len(all_result_dict[tuple()]["data_args"]["topic_list"])
#     logit_spurious = np.random.uniform(low=0.0,high=1.0,size=num_feat)
    logit_spurious = np.ones((num_feat,))
    
    #Now refining the estimate
    overall_spurious_sum = 1.0
    for epoch in range(num_epochs):
        new_temp = 1.0 #+ init_temp/(1.5**epoch)
        prob_spurious = logit_spurious/overall_spurious_sum #/np.sum(logit_spurious)#softmax(logit_spurious/new_temp)
        sprob_list = [float("{:0.2f}".format(prob_spurious[fidx])) for fidx in range(num_feat)]
        
        #Get the spurious subset sample
        spurious_sub = []
        for fidx in range(num_feat):
            if np.random.choice([0,1],p=[1-prob_spurious[fidx],prob_spurious[fidx]])==1:
                spurious_sub.append(fidx)
        #Choosing the spurious subset by sampling from overall distribution
#         spurious_sub = np.random.choice(range(num_feat),size=np.random.randint(num_feat),replace=False,p=prob_spurious).tolist()
#         spurious_sub.sort()
        #Get the other subset
        other_sub = set(range(num_feat)).difference(spurious_sub)
        
        
        #Now getting the scores
        spurious_score = all_result_dict[tuple(spurious_sub)]["ood_meta_dict"]["irm_score"]
#         other_score    = all_result_dict[tuple(other_sub)]["ood_meta_dict"]["irm_score"]
        
        
        #Getting the new the probability
#         spurious_prob = spurious_score / (spurious_score+other_score)
#         other_prob    = 1-spurious_prob 
        
#         #Updating the probability 
#         for fidx in range(num_feat):
#             if(fidx in spurious_sub):
#                 logit_spurious[fidx]+=spurious_score
#             else:
#                 pass
#                 logit_spurious[fidx]+=other_score
        #Converting this back to logits
#         logit_spurious = np.log(prob_spurious+1e-10)
        
        #Getting the individual contribution to the current score
        blame_list=[]
        for fidx in spurious_sub:
            #Get the contribution sfter removing this feature
            removed_sub = list(set(spurious_sub).difference([fidx]))
            removed_sub.sort()
            
            #Getting the difference
            blame = spurious_score - all_result_dict[tuple(removed_sub)]["ood_meta_dict"]["irm_score"]
            blame = blame if blame>0 else 0.0
            
            blame_list.append(blame)
        #Getting the contribution ratio
        blame_list = np.array(blame_list)/(np.sum(blame_list)+1e-10)
        
        #Now distributing the score and updating the probability of these spurious index
        for tidx,fidx in enumerate(spurious_sub):
            logit_spurious[fidx]+=spurious_score*blame_list[tidx] 
        #Adding the spuroiusness score to global score
        overall_spurious_sum += spurious_score
            
        
        
        
        print("sprobs:{}\tssub:{}".format(
                                                                            
                                                                            
                                                                            sprob_list,
                                                                            spurious_sub,
        ))

# Spurious EM

In [156]:
all_result_dict = read_all_result_file()
spurious_by_em(all_result_dict,50)

sprobs:[1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0]	ssub:[0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
sprobs:[0.96, 0.96, 0.96, 0.96, 0.96, 0.96, 0.96, 0.96, 0.97, 0.96]	ssub:[0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
sprobs:[0.91, 0.91, 0.92, 0.91, 0.93, 0.91, 0.93, 0.93, 0.94, 0.93]	ssub:[0, 1, 3, 4, 5, 6, 7, 8, 9]
sprobs:[0.88, 0.88, 0.88, 0.89, 0.9, 0.88, 0.9, 0.89, 0.91, 0.9]	ssub:[0, 1, 2, 4, 5, 6, 7, 8, 9]
sprobs:[0.84, 0.84, 0.85, 0.85, 0.87, 0.86, 0.87, 0.86, 0.88, 0.87]	ssub:[0, 1, 2, 3, 4, 6, 7, 8, 9]
sprobs:[0.81, 0.81, 0.82, 0.82, 0.84, 0.82, 0.83, 0.83, 0.85, 0.83]	ssub:[1, 3, 4, 5, 6, 7, 8, 9]
sprobs:[0.77, 0.78, 0.77, 0.78, 0.8, 0.78, 0.81, 0.79, 0.81, 0.8]	ssub:[0, 3, 4, 5, 6, 7, 8]
sprobs:[0.74, 0.76, 0.75, 0.76, 0.77, 0.76, 0.8, 0.77, 0.79, 0.78]	ssub:[0, 1, 2, 3, 5, 6, 7, 8, 9]
sprobs:[0.72, 0.74, 0.73, 0.76, 0.75, 0.75, 0.78, 0.75, 0.77, 0.76]	ssub:[0, 1, 2, 3, 4, 5, 6, 7, 8, 9]
sprobs:[0.7, 0.72, 0.71, 0.73, 0.73, 0.73, 0.76, 0.73, 0.75, 0.74]	ssub:[2, 4, 5, 6, 7, 8, 9]
sprobs:[0.68,

In [147]:
#Checking the idea that sum of spurious score of a feature will give the probability that its spurious
def get_sprob_by_sum():
    all_result_dict = read_all_result_file()
    num_feat = len(all_result_dict[tuple()]["data_args"]["topic_list"])
    feat_irm_score = np.zeros((num_feat,))

    total_irm_sum = 0.0

    for alive_sub in all_result_dict.keys():
        total_irm_sum += all_result_dict[alive_sub]["ood_meta_dict"]["irm_score"]
        sub_irm_score = all_result_dict[alive_sub]["ood_meta_dict"]["irm_score"]

        #Now checking if any of the feature are there in this subset
        for fidx in range(num_feat):
            if fidx in alive_sub:
                feat_irm_score[fidx]+=all_result_dict[alive_sub]["ood_meta_dict"]["irm_score"]
        
        #Now distributing the blame of this psuriousness on individual feature
#         blame_list=[]
#         for fidx in alive_sub:
#             #Get the contribution sfter removing this feature
#             removed_sub = list(set(alive_sub).difference([fidx]))
#             removed_sub.sort()
            
#             #Getting the difference
#             blame = sub_irm_score - all_result_dict[tuple(removed_sub)]["ood_meta_dict"]["irm_score"]
#             blame = blame if blame>0 else 0.0
            
#             blame_list.append(blame)
#         #Getting the contribution ratio
#         blame_list = np.array(blame_list)/(np.sum(blame_list)+1e-10)
        
#         #Now distributing the score
#         for tidx,fidx in enumerate(alive_sub):
#             feat_irm_score[fidx]+=sub_irm_score*blame_list[tidx]
            

    #Now getting the overall spuriousness probability
    overall_sprob1 = feat_irm_score/total_irm_sum
    overall_sprob2 = feat_irm_score/np.sum(feat_irm_score)
    
    for fidx in range(num_feat):
        print("fidx: {}\tsprob1: {:0.2f}\tsprob2: {:0.2f}".format(fidx,overall_sprob1[fidx],overall_sprob2[fidx]))

get_sprob_by_sum()

fidx: 0	sprob1: 0.45	sprob2: 0.09
fidx: 1	sprob1: 0.50	sprob2: 0.10
fidx: 2	sprob1: 0.48	sprob2: 0.09
fidx: 3	sprob1: 0.51	sprob2: 0.10
fidx: 4	sprob1: 0.50	sprob2: 0.10
fidx: 5	sprob1: 0.59	sprob2: 0.12
fidx: 6	sprob1: 0.56	sprob2: 0.11
fidx: 7	sprob1: 0.49	sprob2: 0.10
fidx: 8	sprob1: 0.54	sprob2: 0.11
fidx: 9	sprob1: 0.52	sprob2: 0.10


In [146]:
#Checking the idea that sum of spurious score of a feature will give the probability that its spurious
def get_sprob_by_sum():
    all_result_dict = read_all_result_file()
    num_feat = len(all_result_dict[tuple()]["data_args"]["topic_list"])
    feat_irm_score = np.zeros((num_feat,))

    total_irm_sum = 0.0

    for alive_sub in all_result_dict.keys():
        total_irm_sum += all_result_dict[alive_sub]["ood_meta_dict"]["irm_score"]
        sub_irm_score = all_result_dict[alive_sub]["ood_meta_dict"]["irm_score"]

        #Now checking if any of the feature are there in this subset
#         for fidx in range(num_feat):
#             if fidx in alive_sub:
#                 feat_irm_score[fidx]+=all_result_dict[alive_sub]["ood_meta_dict"]["irm_score"]
        
        #Now distributing the blame of this psuriousness on individual feature
        blame_list=[]
        for fidx in alive_sub:
            #Get the contribution sfter removing this feature
            removed_sub = list(set(alive_sub).difference([fidx]))
            removed_sub.sort()
            
            #Getting the difference
            blame = sub_irm_score - all_result_dict[tuple(removed_sub)]["ood_meta_dict"]["irm_score"]
            blame = blame if blame>0 else 0.0
            
            blame_list.append(blame)
        #Getting the contribution ratio
        blame_list = np.array(blame_list)/(np.sum(blame_list)+1e-10)
        
        #Now distributing the score
        for tidx,fidx in enumerate(alive_sub):
            feat_irm_score[fidx]+=sub_irm_score*blame_list[tidx]
            

    #Now getting the overall spuriousness probability
    overall_sprob1 = feat_irm_score/total_irm_sum
    overall_sprob2 = feat_irm_score/np.sum(feat_irm_score)
    
    for fidx in range(num_feat):
        print("fidx: {}\tsprob1: {:0.2f}\tsprob2: {:0.2f}".format(fidx,overall_sprob1[fidx],overall_sprob2[fidx]))

get_sprob_by_sum()

fidx: 0	sprob1: 0.04	sprob2: 0.05
fidx: 1	sprob1: 0.07	sprob2: 0.07
fidx: 2	sprob1: 0.05	sprob2: 0.05
fidx: 3	sprob1: 0.06	sprob2: 0.07
fidx: 4	sprob1: 0.06	sprob2: 0.06
fidx: 5	sprob1: 0.26	sprob2: 0.27
fidx: 6	sprob1: 0.15	sprob2: 0.15
fidx: 7	sprob1: 0.06	sprob2: 0.06
fidx: 8	sprob1: 0.13	sprob2: 0.13
fidx: 9	sprob1: 0.08	sprob2: 0.09


# IRM Score

In [48]:
all_result_dict = read_all_result_file()
all_result_list = [(key,all_result_dict[key]["ood_meta_dict"]["irm_score"]) for key in all_result_dict.keys()]
all_result_list.sort(key=lambda x:x[-1])
all_result_list[-1000:]

Getting spurousness score for:[1, 3, 5, 7, 9]
Perf Better than optimal perf:	curr:arts	other:clothes	drop:0.01843315362930298
Perf Better than optimal perf:	curr:books	other:arts	drop:0.01612907648086548
Perf Better than optimal perf:	curr:books	other:phones	drop:0.01612907648086548
Perf Better than optimal perf:	curr:books	other:groceries	drop:0.01612907648086548
Perf Better than optimal perf:	curr:books	other:tools	drop:0.023041486740112305
Perf Better than optimal perf:	curr:groceries	other:tools	drop:0.0023041963577270508
Perf Better than optimal perf:	curr:movies	other:books	drop:0.02534562349319458
Perf Better than optimal perf:	curr:pets	other:arts	drop:0.02534562349319458
Perf Better than optimal perf:	curr:pets	other:phones	drop:0.02534562349319458
Perf Better than optimal perf:	curr:pets	other:groceries	drop:0.02534562349319458
Perf Better than optimal perf:	curr:pets	other:tools	drop:0.023041486740112305
Getting spurousness score for:[0, 1, 2, 3, 6, 7]
Perf Better than optim

Getting spurousness score for:[2, 8, 9]
Perf Better than optimal perf:	curr:arts	other:clothes	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:groceries	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:movies	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:phones	other:arts	drop:0.0069124698638916016
Perf Better than optimal perf:	curr:phones	other:books	drop:0.0069124698638916016
Perf Better than optimal perf:	curr:phones	other:clothes	drop:0.004608273506164551
Perf Better than optimal perf:	curr:phones	other:groceries	drop:0.004608273506164551
Perf Better than optimal perf:	curr:phones	other:movies	drop:0.004608273506164551
Perf Better than optimal perf:	curr:phones	other:tools	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:clothes	other:phones	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:clothes	other:pets	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:groceries	other:

Getting spurousness score for:[0, 3]
Perf Better than optimal perf:	curr:arts	other:books	drop:0.006912410259246826
Perf Better than optimal perf:	curr:arts	other:movies	drop:0.006912410259246826
Perf Better than optimal perf:	curr:arts	other:pets	drop:0.006912410259246826
Perf Better than optimal perf:	curr:pets	other:arts	drop:0.004608273506164551
Perf Better than optimal perf:	curr:pets	other:phones	drop:0.004608273506164551
Perf Better than optimal perf:	curr:pets	other:clothes	drop:0.004608273506164551
Perf Better than optimal perf:	curr:pets	other:groceries	drop:0.004608273506164551
Perf Better than optimal perf:	curr:pets	other:tools	drop:0.004608273506164551
Perf Better than optimal perf:	curr:tools	other:books	drop:0.018433213233947754
Perf Better than optimal perf:	curr:tools	other:movies	drop:0.018433213233947754
Perf Better than optimal perf:	curr:tools	other:pets	drop:0.018433213233947754
Getting spurousness score for:[0, 2, 4, 7, 9]
Perf Better than optimal perf:	curr:boo

Getting spurousness score for:[4, 7]
Perf Better than optimal perf:	curr:arts	other:books	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:phones	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:groceries	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:movies	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:pets	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:tools	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:clothes	other:arts	drop:0.029953956604003906
Perf Better than optimal perf:	curr:clothes	other:books	drop:0.029953956604003906
Perf Better than optimal perf:	curr:clothes	other:phones	drop:0.029953956604003906
Perf Better than optimal perf:	curr:clothes	other:groceries	drop:0.029953956604003906
Perf Better than optimal perf:	curr:clothes	other:movies	drop:0.029953956604003906
Perf Better than optimal perf:	curr:clothes	other:pets	drop:0.0

Getting spurousness score for:[0, 1, 5, 6, 7, 9]
Perf Better than optimal perf:	curr:phones	other:arts	drop:0.01612907648086548
Perf Better than optimal perf:	curr:phones	other:books	drop:0.02764981985092163
Perf Better than optimal perf:	curr:phones	other:groceries	drop:0.011520743370056152
Perf Better than optimal perf:	curr:phones	other:movies	drop:0.0069124698638916016
Perf Better than optimal perf:	curr:movies	other:books	drop:0.018433213233947754
Perf Better than optimal perf:	curr:pets	other:arts	drop:0.052995383739471436
Perf Better than optimal perf:	curr:pets	other:books	drop:0.05069124698638916
Perf Better than optimal perf:	curr:pets	other:phones	drop:0.052995383739471436
Perf Better than optimal perf:	curr:pets	other:clothes	drop:0.04147464036941528
Perf Better than optimal perf:	curr:pets	other:groceries	drop:0.05069124698638916
Perf Better than optimal perf:	curr:pets	other:movies	drop:0.052995383739471436
Perf Better than optimal perf:	curr:pets	other:tools	drop:0.05529

...

Getting spurousness score for:[1, 6, 8]
Perf Better than optimal perf:	curr:arts	other:books	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:phones	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:clothes	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:groceries	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:pets	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:tools	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:phones	other:arts	drop:0.055299580097198486
Perf Better than optimal perf:	curr:phones	other:books	drop:0.055299580097198486
Perf Better than optimal perf:	curr:phones	other:movies	drop:0.055299580097198486
Perf Better than optimal perf:	curr:phones	other:pets	drop:0.055299580097198486
Perf Better than optimal perf:	curr:groceries	other:arts	drop:0.0023041963577270508
Perf Better than optimal perf:	curr:groceries	other:books	drop:0.08

Getting spurousness score for:[0, 2, 3, 6, 7, 9]
Perf Better than optimal perf:	curr:arts	other:books	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:movies	drop:0.004608273506164551
Perf Better than optimal perf:	curr:arts	other:pets	drop:0.004608273506164551
Perf Better than optimal perf:	curr:arts	other:tools	drop:0.004608273506164551
Perf Better than optimal perf:	curr:phones	other:books	drop:0.023041486740112305
Perf Better than optimal perf:	curr:phones	other:groceries	drop:0.02534562349319458
Perf Better than optimal perf:	curr:phones	other:movies	drop:0.018433213233947754
Perf Better than optimal perf:	curr:movies	other:books	drop:0.009216606616973877
Perf Better than optimal perf:	curr:pets	other:arts	drop:0.004608273506164551
Perf Better than optimal perf:	curr:pets	other:phones	drop:0.004608273506164551
Getting spurousness score for:[0, 1, 3, 4, 6, 7, 8, 9]
Perf Better than optimal perf:	curr:arts	other:phones	drop:0.023041486740112305
Perf Better t

Perf Better than optimal perf:	curr:clothes	other:arts	drop:0.013824880123138428
Perf Better than optimal perf:	curr:clothes	other:books	drop:0.020737290382385254
Perf Better than optimal perf:	curr:clothes	other:phones	drop:0.016129016876220703
Perf Better than optimal perf:	curr:clothes	other:groceries	drop:0.013824880123138428
Perf Better than optimal perf:	curr:clothes	other:pets	drop:0.016129016876220703
Perf Better than optimal perf:	curr:clothes	other:tools	drop:0.016129016876220703
Perf Better than optimal perf:	curr:movies	other:arts	drop:0.03456223011016846
Perf Better than optimal perf:	curr:movies	other:books	drop:0.02764981985092163
Perf Better than optimal perf:	curr:movies	other:groceries	drop:0.03456223011016846
Perf Better than optimal perf:	curr:movies	other:pets	drop:0.03686636686325073
Perf Better than optimal perf:	curr:movies	other:tools	drop:0.03686636686325073
Getting spurousness score for:[0, 2, 5, 9]
Perf Better than optimal perf:	curr:arts	other:movies	drop:0

Getting spurousness score for:[1, 3, 6, 9]
Perf Better than optimal perf:	curr:arts	other:books	drop:0.011520743370056152
Perf Better than optimal perf:	curr:arts	other:phones	drop:0.011520743370056152
Perf Better than optimal perf:	curr:arts	other:clothes	drop:0.013824880123138428
Perf Better than optimal perf:	curr:arts	other:groceries	drop:0.011520743370056152
Perf Better than optimal perf:	curr:arts	other:pets	drop:0.011520743370056152
Perf Better than optimal perf:	curr:arts	other:tools	drop:0.013824880123138428
Perf Better than optimal perf:	curr:movies	other:books	drop:0.013824880123138428
Perf Better than optimal perf:	curr:movies	other:phones	drop:0.013824880123138428
Perf Better than optimal perf:	curr:movies	other:groceries	drop:0.013824880123138428
Perf Better than optimal perf:	curr:movies	other:pets	drop:0.013824880123138428
Perf Better than optimal perf:	curr:pets	other:arts	drop:0.009216606616973877
Perf Better than optimal perf:	curr:pets	other:clothes	drop:0.011520743

[((2, 3, 4, 8), 0.008105670767171043),
 ((1, 3, 4), 0.008393682539463043),
 ((2, 3, 4), 0.008558259478637151),
 ((1, 2, 3, 4, 8), 0.010204083153179713),
 ((0, 1, 3, 7, 9), 0.010245226323604584),
 ((0, 1, 2, 3, 7, 9), 0.01036866647856576),
 ((1, 4, 8), 0.010368674993515015),
 ((1, 3, 4, 8), 0.010492098118577684),
 ((0, 1, 4, 7, 9), 0.010492102376052312),
 ((2, 7, 8, 9), 0.010533255125795091),
 ((1, 3, 9), 0.010903550045830863),
 ((0, 4, 7, 9), 0.011026991265160697),
 ((2, 3, 8), 0.01119157884802137),
 ((0, 6), 0.011520735387291228),
 ((0, 1, 4, 6, 7), 0.011644171816962106),
 ((0, 4, 6), 0.011767615697213582),
 ((2, 3, 6), 0.012179072414125715),
 ((0, 3, 4, 7), 0.01238479997430529),
 ((2, 8, 9), 0.01267281493970326),
 ((1, 6), 0.013331140790666853),
 ((0, 1, 2, 6), 0.013454572430678777),
 ((0, 2, 3, 8), 0.0135368640933718),
 ((1, 8, 9), 0.013660307441438948),
 ((0, 3, 7), 0.013701439968177251),
 ((0, 3, 4, 6), 0.013701451144048147),
 ((0, 7, 9), 0.013701451676232474),
 ((1, 8), 0.0138660

In [49]:
all_result_dict = read_all_result_file()
all_result_list = [(key,all_result_dict[key]["ood_meta_dict"]["irm_score"]) for key in all_result_dict.keys() if len(key)==1]
all_result_list.sort(key=lambda x:x[-1])
all_result_list[-1000:]

Getting spurousness score for:[1, 3, 5, 7, 9]
Perf Better than optimal perf:	curr:arts	other:clothes	drop:0.01843315362930298
Perf Better than optimal perf:	curr:books	other:arts	drop:0.01612907648086548
Perf Better than optimal perf:	curr:books	other:phones	drop:0.01612907648086548
Perf Better than optimal perf:	curr:books	other:groceries	drop:0.01612907648086548
Perf Better than optimal perf:	curr:books	other:tools	drop:0.023041486740112305
Perf Better than optimal perf:	curr:groceries	other:tools	drop:0.0023041963577270508
Perf Better than optimal perf:	curr:movies	other:books	drop:0.02534562349319458
Perf Better than optimal perf:	curr:pets	other:arts	drop:0.02534562349319458
Perf Better than optimal perf:	curr:pets	other:phones	drop:0.02534562349319458
Perf Better than optimal perf:	curr:pets	other:groceries	drop:0.02534562349319458
Perf Better than optimal perf:	curr:pets	other:tools	drop:0.023041486740112305
Getting spurousness score for:[0, 1, 2, 3, 6, 7]
Perf Better than optim

Perf Better than optimal perf:	curr:phones	other:tools	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:clothes	other:phones	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:clothes	other:pets	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:groceries	other:arts	drop:0.0023041963577270508
Perf Better than optimal perf:	curr:groceries	other:books	drop:0.0023041963577270508
Getting spurousness score for:[2, 3, 4, 6, 7, 8, 9]
Perf Better than optimal perf:	curr:arts	other:books	drop:0.011520743370056152
Perf Better than optimal perf:	curr:arts	other:phones	drop:0.0023041963577270508
Perf Better than optimal perf:	curr:arts	other:groceries	drop:0.004608333110809326
Perf Better than optimal perf:	curr:arts	other:tools	drop:0.011520743370056152
Perf Better than optimal perf:	curr:clothes	other:arts	drop:0.013824880123138428
Perf Better than optimal perf:	curr:clothes	other:books	drop:0.013824880123138428
Perf Better than optimal perf:	curr:clothes	ot

Perf Better than optimal perf:	curr:groceries	other:arts	drop:0.01843315362930298
Perf Better than optimal perf:	curr:groceries	other:books	drop:0.05069124698638916
Perf Better than optimal perf:	curr:groceries	other:phones	drop:0.013824880123138428
Perf Better than optimal perf:	curr:groceries	other:clothes	drop:0.052995383739471436
Perf Better than optimal perf:	curr:groceries	other:movies	drop:0.03686636686325073
Perf Better than optimal perf:	curr:groceries	other:pets	drop:0.048387110233306885
Perf Better than optimal perf:	curr:groceries	other:tools	drop:0.052995383739471436
Perf Better than optimal perf:	curr:movies	other:books	drop:0.004608273506164551
Perf Better than optimal perf:	curr:movies	other:clothes	drop:0.006912410259246826
Perf Better than optimal perf:	curr:movies	other:tools	drop:0.023041486740112305
Perf Better than optimal perf:	curr:pets	other:tools	drop:0.0023041367530822754
Getting spurousness score for:[3, 4, 6, 9]
Perf Better than optimal perf:	curr:arts	othe

Getting spurousness score for:[0, 1, 3, 6, 7]
Perf Better than optimal perf:	curr:arts	other:tools	drop:0.004608333110809326
Perf Better than optimal perf:	curr:books	other:arts	drop:0.03686636686325073
Perf Better than optimal perf:	curr:books	other:phones	drop:0.03686636686325073
Perf Better than optimal perf:	curr:books	other:groceries	drop:0.02534562349319458
Perf Better than optimal perf:	curr:books	other:movies	drop:0.03917050361633301
Perf Better than optimal perf:	curr:books	other:tools	drop:0.027649760246276855
Perf Better than optimal perf:	curr:groceries	other:arts	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:groceries	other:phones	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:groceries	other:movies	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:groceries	other:tools	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:movies	other:books	drop:0.06221199035644531
Getting spurousness score for:[1, 2, 5, 8]
Perf Bette

Getting spurousness score for:[0, 1, 2, 4, 6, 7, 8]
Perf Better than optimal perf:	curr:arts	other:books	drop:0.023041486740112305
Perf Better than optimal perf:	curr:arts	other:phones	drop:0.027649760246276855
Perf Better than optimal perf:	curr:arts	other:groceries	drop:0.027649760246276855
Perf Better than optimal perf:	curr:arts	other:movies	drop:0.02534562349319458
Perf Better than optimal perf:	curr:arts	other:pets	drop:0.027649760246276855
Perf Better than optimal perf:	curr:arts	other:tools	drop:0.013824880123138428
Perf Better than optimal perf:	curr:phones	other:arts	drop:0.0023041963577270508
Perf Better than optimal perf:	curr:phones	other:books	drop:0.02073734998703003
Perf Better than optimal perf:	curr:phones	other:groceries	drop:0.0023041963577270508
Perf Better than optimal perf:	curr:phones	other:movies	drop:0.023041486740112305
Perf Better than optimal perf:	curr:pets	other:groceries	drop:0.0023041367530822754
Getting spurousness score for:[0, 4, 5, 6, 8, 9]
Perf Bet

...

Getting spurousness score for:[0, 3, 4, 5, 7, 9]
Perf Better than optimal perf:	curr:books	other:pets	drop:0.01843315362930298
Perf Better than optimal perf:	curr:phones	other:arts	drop:0.01612907648086548
Perf Better than optimal perf:	curr:phones	other:clothes	drop:0.01612907648086548
Perf Better than optimal perf:	curr:phones	other:groceries	drop:0.01612907648086548
Perf Better than optimal perf:	curr:groceries	other:arts	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:movies	other:books	drop:0.055299580097198486
Perf Better than optimal perf:	curr:movies	other:pets	drop:0.03686636686325073
Perf Better than optimal perf:	curr:pets	other:arts	drop:0.011520683765411377
Perf Better than optimal perf:	curr:pets	other:phones	drop:0.02304142713546753
Perf Better than optimal perf:	curr:pets	other:clothes	drop:0.020737290382385254
Perf Better than optimal perf:	curr:pets	other:groceries	drop:0.016129016876220703
Perf Better than optimal perf:	curr:pets	other:movies	drop:0.00

Getting spurousness score for:[0, 2, 3, 4, 5, 6]
Perf Better than optimal perf:	curr:arts	other:books	drop:0.004608273506164551
Perf Better than optimal perf:	curr:books	other:groceries	drop:0.009216547012329102
Perf Better than optimal perf:	curr:books	other:tools	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:phones	other:arts	drop:0.032258033752441406
Perf Better than optimal perf:	curr:phones	other:books	drop:0.020737290382385254
Perf Better than optimal perf:	curr:phones	other:groceries	drop:0.009216606616973877
Perf Better than optimal perf:	curr:groceries	other:arts	drop:0.009216547012329102
Perf Better than optimal perf:	curr:groceries	other:phones	drop:0.011520683765411377
Perf Better than optimal perf:	curr:groceries	other:pets	drop:0.006912410259246826
Perf Better than optimal perf:	curr:groceries	other:tools	drop:0.011520683765411377
Perf Better than optimal perf:	curr:pets	other:phones	drop:0.004608273506164551
Getting spurousness score for:[0, 2, 3, 4, 7, 

Getting spurousness score for:[2, 5, 8, 9]
Perf Better than optimal perf:	curr:arts	other:groceries	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:movies	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:pets	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:groceries	other:arts	drop:0.004608333110809326
Perf Better than optimal perf:	curr:groceries	other:books	drop:0.0023041963577270508
Perf Better than optimal perf:	curr:groceries	other:phones	drop:0.0023041963577270508
Perf Better than optimal perf:	curr:pets	other:groceries	drop:0.011520743370056152
Perf Better than optimal perf:	curr:pets	other:movies	drop:0.0023041367530822754
Getting spurousness score for:[1, 3, 8, 9]
Perf Better than optimal perf:	curr:phones	other:arts	drop:0.02073734998703003
Perf Better than optimal perf:	curr:phones	other:books	drop:0.02073734998703003
Perf Better than optimal perf:	curr:phones	other:clothes	drop:0.013824939727783203
Perf Bette

Getting spurousness score for:[0, 3, 4, 8, 9]
Perf Better than optimal perf:	curr:arts	other:phones	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:pets	drop:0.006912410259246826
Perf Better than optimal perf:	curr:arts	other:tools	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:books	other:phones	drop:0.006912410259246826
Perf Better than optimal perf:	curr:books	other:movies	drop:0.009216606616973877
Perf Better than optimal perf:	curr:books	other:pets	drop:0.01843315362930298
Perf Better than optimal perf:	curr:books	other:tools	drop:0.013824880123138428
Perf Better than optimal perf:	curr:groceries	other:phones	drop:0.009216606616973877
Perf Better than optimal perf:	curr:groceries	other:clothes	drop:0.009216606616973877
Perf Better than optimal perf:	curr:groceries	other:pets	drop:0.02534562349319458
Perf Better than optimal perf:	curr:groceries	other:tools	drop:0.009216606616973877
Perf Better than optimal perf:	curr:tools	other:pets	drop:

[((0,), 0.0),
 ((1,), 0.0),
 ((7,), 0.0),
 ((2,), 0.0),
 ((4,), 0.01431863276021821),
 ((3,), 0.014400925487279892),
 ((9,), 0.021066493753876005),
 ((6,), 0.034027318337133954),
 ((8,), 0.04147465101310185),
 ((5,), 0.06163595084633146)]

# Overall Drop

In [4]:
all_result_dict = read_all_result_file()
all_result_list = [(key,all_result_dict[key]["ood_meta_dict"]["overall_ood_drop"]) for key in all_result_dict.keys()]
all_result_list.sort(key=lambda x:x[-1])
all_result_list

[((4, 5, 6, 8), -4.562211990356445),
 ((1, 3, 5, 6, 7, 8, 9), -4.476959228515625),
 ((1, 4, 5, 6, 7, 8, 9), -4.373271942138672),
 ((1, 3, 4, 5, 6, 8, 9), -4.368663787841797),
 ((3, 5, 6, 8), -4.3594465255737305),
 ((5, 6, 7, 8, 9), -4.354838848114014),
 ((3, 5, 6, 8, 9), -4.3548383712768555),
 ((1, 3, 4, 5, 6, 8), -4.311059474945068),
 ((5, 6, 8), -4.29262638092041),
 ((1, 3, 4, 5, 6, 7, 8, 9), -4.288018226623535),
 ((1, 4, 5, 6, 8, 9), -4.278801918029785),
 ((3, 4, 5, 6, 9), -4.218894004821777),
 ((5, 6, 8, 9), -4.168202877044678),
 ((4, 5, 6, 9), -4.105990409851074),
 ((1, 5, 6, 8, 9), -4.103686809539795),
 ((3, 5, 6, 7, 8, 9), -4.09907865524292),
 ((4, 5, 8), -4.052995204925537),
 ((4, 5, 6, 7, 8, 9), -4.0506911277771),
 ((1, 3, 5, 6, 8), -4.050690650939941),
 ((3, 4, 5, 6, 8, 9), -4.046082496643066),
 ((1, 3, 4, 5, 6), -4.039170265197754),
 ((1, 3, 5, 6, 8, 9), -4.034562110900879),
 ((1, 3, 5, 6, 9), -4.032257080078125),
 ((4, 5, 6, 8, 9), -4.025345802307129),
 ((3, 5, 6, 7, 9), -4

In [205]:
all_result_dict = read_all_result_file()
all_result_list = [(key,all_result_dict[key]["ood_meta_dict"]["mean_ood_drop"]) for key in all_result_dict.keys() if len(key)==1]
all_result_list.sort(key=lambda x:x[-1])
all_result_list[0:1000]

[((5,), -0.09224534779787064),
 ((8,), -0.06212335824966431),
 ((2,), -0.054641205817461014),
 ((0,), -0.05134955793619156),
 ((7,), -0.04814021661877632),
 ((1,), -0.04429084435105324),
 ((6,), -0.04352278262376785),
 ((9,), -0.035463832318782806),
 ((3,), -0.019835708662867546),
 ((4,), -0.018190648406744003)]

In [206]:
all_result_dict = read_all_result_file()
all_result_list = [(key,all_result_dict[key]["ood_meta_dict"]["overall_ood_drop"]) for key in all_result_dict.keys() if len(key)==1]
all_result_list.sort(key=lambda x:x[-1])
all_result_list[0:1000]

[((5,), -2.6751151084899902),
 ((8,), -1.615207314491272),
 ((6,), -1.5668201446533203),
 ((2,), -1.5299537181854248),
 ((0,), -1.437787652015686),
 ((7,), -1.3479260206222534),
 ((1,), -1.1958527565002441),
 ((9,), -0.8156681060791016),
 ((3,), -0.4562213122844696),
 ((4,), -0.34562233090400696)]

# Overall Average

In [171]:
all_result_dict = read_all_result_file()
all_result_list = [(key,all_result_dict[key]["ood_meta_dict"]["mean_all_vacc"]) for key in all_result_dict.keys() if len(key)==1]
all_result_list.sort(key=lambda x:x[-1])
all_result_list[-1000:]

[((4,), 0.49150344729423523),
 ((6,), 0.49996399879455566),
 ((9,), 0.5038882493972778),
 ((3,), 0.5045362710952759),
 ((8,), 0.5106566548347473),
 ((5,), 0.5498992204666138),
 ((1,), 0.5561635494232178),
 ((7,), 0.5895737409591675),
 ((0,), 0.6036866307258606),
 ((2,), 0.639976978302002)]

In [201]:
all_result_dict = read_all_result_file()
all_result_list = [(key,all_result_dict[key]["ood_meta_dict"]["mean_all_vacc"]) for key in all_result_dict.keys()]
all_result_list.sort(key=lambda x:x[-1])
all_result_list[-1000:]

[((3, 4, 8), 0.5181811451911926),
 ((3, 4, 6, 9), 0.5191532373428345),
 ((8, 9), 0.5201972723007202),
 ((3, 6, 9), 0.5202332735061646),
 ((4, 5, 8, 9), 0.5214213728904724),
 ((3, 4, 6, 8), 0.5233654975891113),
 ((3, 6, 8, 9), 0.525813639163971),
 ((4, 5, 8), 0.5264257192611694),
 ((4, 7, 8), 0.5312139987945557),
 ((5, 6, 8), 0.5325100421905518),
 ((5, 6, 9), 0.5328341126441956),
 ((3, 4, 8, 9), 0.5346702337265015),
 ((7, 9), 0.5378744602203369),
 ((4, 5, 6, 8), 0.5381264686584473),
 ((5, 8), 0.5385944843292236),
 ((3, 5, 6, 9), 0.5395665168762207),
 ((4, 5, 6, 7, 8), 0.5405386090278625),
 ((1, 4, 7, 8), 0.5407186150550842),
 ((4, 5, 6, 9), 0.5410426259040833),
 ((3, 8, 9), 0.5423387289047241),
 ((5, 6, 7, 8, 9), 0.5423747301101685),
 ((3, 4, 5, 6), 0.5427347421646118),
 ((3, 5, 6), 0.5429508090019226),
 ((3, 4, 7, 9), 0.5439947843551636),
 ((3, 5, 8, 9), 0.5440307855606079),
 ((3, 4, 5, 6, 9), 0.5442467927932739),
 ((4, 5, 6, 8, 9), 0.544282853603363),
 ((3, 5, 8), 0.5448588728904724),

# OOD Average

In [186]:
all_result_dict = read_all_result_file()
num_cat = len(all_result_dict[()]["data_args"]["cat_list"])
all_result_list = [
                    (
                        key,
                        (  (all_result_dict[key]["ood_meta_dict"]["mean_all_vacc"]*(num_cat**2)) - (all_result_dict[key]["ood_meta_dict"]["mean_indo_vacc"]*(num_cat))    )/(num_cat*(num_cat-1))
                    ) 
                               for key in all_result_dict.keys() if len(key)==1
                  ]
all_result_list.sort(key=lambda x:x[-1])
all_result_list[-1000:]

[((4,), 0.4922234926904951),
 ((6,), 0.49790158442088533),
 ((9,), 0.503785388810294),
 ((3,), 0.5051431655883789),
 ((8,), 0.5097926003592355),
 ((5,), 0.546329847403935),
 ((1,), 0.5561635494232178),
 ((7,), 0.5895737409591675),
 ((0,), 0.6036866307258606),
 ((2,), 0.639976978302002)]

In [188]:
all_result_dict = read_all_result_file()
num_cat = len(all_result_dict[()]["data_args"]["cat_list"])
all_result_list = [
                    (
                        key,
                        (  (all_result_dict[key]["ood_meta_dict"]["mean_all_vacc"]*(num_cat**2)) - (all_result_dict[key]["ood_meta_dict"]["mean_indo_vacc"]*(num_cat))    )/(num_cat*(num_cat-1))
                    ) 
                               for key in all_result_dict.keys()
                  ]
all_result_list.sort(key=lambda x:x[-1])
all_result_list[-1000:]

[((3, 4, 8), 0.515882134437561),
 ((3, 4, 9), 0.5160467198916844),
 ((3, 4, 6, 9), 0.5161290424210685),
 ((8, 9), 0.5185154506138393),
 ((4, 5, 8), 0.5185155017035348),
 ((3, 6, 9), 0.5189680542264666),
 ((3, 4, 6, 8), 0.519544107573373),
 ((3, 6, 8, 9), 0.5202847123146057),
 ((5, 6, 8), 0.5240289313452584),
 ((5, 6, 9), 0.5256748029163906),
 ((4, 7, 8), 0.5266622815813337),
 ((4, 5, 6, 8), 0.5295013529913766),
 ((5, 8), 0.5324638060161045),
 ((3, 4, 8, 9), 0.5330809865679059),
 ((4, 5, 6, 9), 0.5333689962114606),
 ((4, 5, 6, 7, 8), 0.5333690132413592),
 ((3, 5, 6, 9), 0.5334101234163556),
 ((5, 6, 7, 8, 9), 0.5341919234820774),
 ((3, 4, 5, 6, 9), 0.5363725679261344),
 ((4, 5, 6, 8, 9), 0.5365783657346453),
 ((7, 9), 0.5367429597037179),
 ((3, 5, 6), 0.5370310119220189),
 ((3, 5, 8), 0.5375658358846392),
 ((3, 5, 8, 9), 0.5377715229988098),
 ((3, 4, 5, 6), 0.5385944758142743),
 ((5, 7, 8), 0.5388413412230355),
 ((3, 5, 6, 8, 9), 0.5391704865864345),
 ((6, 7, 8), 0.5393350975854057),
 (

# Indo Average

In [170]:
all_result_dict = read_all_result_file()
all_result_list = [(key,all_result_dict[key]["ood_meta_dict"]["mean_indo_vacc"]) for key in all_result_dict.keys() if len(key)==1]
all_result_list.sort(key=lambda x:x[-1])
all_result_list[-1000:]

[((4,), 0.48646312952041626),
 ((3,), 0.5002880096435547),
 ((9,), 0.5046082735061646),
 ((6,), 0.5144008994102478),
 ((8,), 0.5167050361633301),
 ((1,), 0.5561635494232178),
 ((5,), 0.574884831905365),
 ((7,), 0.5895737409591675),
 ((0,), 0.6036866307258606),
 ((2,), 0.639976978302002)]

In [210]:
all_result_dict = read_all_result_file()
all_result_list = [(key,all_result_dict[key]["ood_meta_dict"]["mean_indo_vacc"]) for key in all_result_dict.keys()]
all_result_list.sort(key=lambda x:x[-1])
all_result_list#[-1000:]

[((), 0.4861750900745392),
 ((4,), 0.48646312952041626),
 ((3,), 0.5002880096435547),
 ((9,), 0.5046082735061646),
 ((4, 9), 0.5066244602203369),
 ((3, 4), 0.5069124698638916),
 ((6,), 0.5144008994102478),
 ((4, 8), 0.5144009590148926),
 ((3, 4, 6), 0.514976978302002),
 ((4, 6), 0.5161290168762207),
 ((8,), 0.5167050361633301),
 ((3, 4, 9), 0.5181451439857483),
 ((3, 9), 0.5227534770965576),
 ((4, 6, 9), 0.5262097120285034),
 ((3, 6), 0.5264977216720581),
 ((6, 9), 0.5264977216720581),
 ((3, 6, 9), 0.5290898084640503),
 ((3, 8), 0.5313940048217773),
 ((8, 9), 0.5319700241088867),
 ((3, 4, 8), 0.5342742204666138),
 ((4, 8, 9), 0.5360022783279419),
 ((3, 4, 6, 9), 0.5403226017951965),
 ((6, 8), 0.544066846370697),
 ((4, 6, 8), 0.5443548560142517),
 ((7, 9), 0.5457949638366699),
 ((3, 4, 8, 9), 0.5457949638366699),
 ((1, 4, 7, 8), 0.550115168094635),
 ((3, 4, 6, 8), 0.5501152276992798),
 ((3, 8, 9), 0.5506912469863892),
 ((3, 6, 7), 0.5515552759170532),
 ((3, 4, 7, 9), 0.5518432855606079)

### Getting metric for useless 

In [53]:
all_result_dict = read_all_result_file()
all_result_list = [(key,all_result_dict[key]["ood_meta_dict"]["mean_indo_vacc"]) 
                       for key in all_result_dict.keys()
                               if all_result_dict[key]["ood_meta_dict"]["mean_indo_vacc"]<0.52
                  ]
all_result_list.sort(key=lambda x:len(x[0]))
all_result_list#[-1000:]

[((), 0.4861751087009907),
 ((9,), 0.5046082995831966),
 ((3,), 0.5002880096435547),
 ((8,), 0.5167050659656525),
 ((4,), 0.48646313324570656),
 ((6,), 0.514400914311409),
 ((3, 4), 0.5069124437868595),
 ((4, 6), 0.5161290280520916),
 ((4, 9), 0.5066244266927242),
 ((4, 8), 0.5144009180366993),
 ((3, 4, 9), 0.5181451551616192),
 ((3, 4, 6), 0.5149769559502602)]

### Getting corrected ood vacc only

In [189]:
all_result_dict = read_all_result_file()
all_result_list = [(key,all_result_dict[key]["ood_meta_dict"]["mean_all_vacc"]-all_result_dict[key]["ood_meta_dict"]["mean_indo_vacc"]) for key in all_result_dict.keys() if len(key)==1]
all_result_list.sort(key=lambda x:x[-1])
all_result_list[-1000:]

[((5,), -0.02498561143875122),
 ((6,), -0.014436900615692139),
 ((8,), -0.006048381328582764),
 ((9,), -0.0007200241088867188),
 ((0,), 0.0),
 ((1,), 0.0),
 ((7,), 0.0),
 ((2,), 0.0),
 ((3,), 0.004248261451721191),
 ((4,), 0.00504031777381897)]

In [4]:
all_result_dict = read_all_result_file()
all_result_list = [(key,all_result_dict[key]["ood_meta_dict"]["mean_all_vacc"]-all_result_dict[key]["ood_meta_dict"]["mean_indo_vacc"]) for key in all_result_dict.keys()]
all_result_list.sort(key=lambda x:x[-1])
all_result_list[-1000:]

[((5, 6, 9), -0.05011519975960255),
 ((5, 6, 7, 8), -0.049899190198630095),
 ((5, 6, 8, 9), -0.04979118425399065),
 ((3, 4, 5, 6, 7, 8), -0.04917914140969515),
 ((3, 4, 5, 8), -0.04896312905475497),
 ((1, 2, 4, 5, 6, 7, 9), -0.04871111921966076),
 ((3, 4, 6, 8, 9), -0.0486751152202487),
 ((1, 5, 6), -0.048171079717576504),
 ((1, 5, 6, 7, 9), -0.047775063663721085),
 ((1, 3, 5, 6, 9), -0.04770304262638092),
 ((3, 4, 5, 6, 8, 9), -0.047595041804015636),
 ((1, 4, 5, 6, 7, 8), -0.046947012189775705),
 ((3, 4, 5, 7, 8, 9), -0.046838991809636354),
 ((1, 2, 3, 4, 5, 6, 8, 9), -0.046730995643883944),
 ((1, 3, 5, 6, 8, 9), -0.04662298457697034),
 ((1, 5, 7, 8, 9), -0.04651498468592763),
 ((3, 4, 5, 6, 8), -0.04647896718233824),
 ((1, 2, 5, 6, 7, 8, 9), -0.046406968496739864),
 ((4, 5, 7, 8), -0.04633495910093188),
 ((0, 3, 5, 6, 7, 8, 9), -0.04611894302070141),
 ((1, 4, 5, 6), -0.04604694340378046),
 ((3, 4, 5, 8, 9), -0.046010943595319986),
 ((0, 5, 6, 8, 9), -0.045866938307881355),
 ((4, 5, 6

# New Causal Score

In [159]:
all_result_dict = read_all_result_file()
all_result_list = [
                    (
                        key,
                        all_result_dict[key]["ood_meta_dict"]["mean_indo_vacc"]*(1-abs(all_result_dict[key]["ood_meta_dict"]["mean_ood_drop"]))
                    ) 
                               for key in all_result_dict.keys()
                  ]
all_result_list.sort(key=lambda x:x[-1])
all_result_list[-1000:]

[((1, 4, 7, 8), 0.5097486879571758),
 ((4, 6, 8, 9), 0.511180764813143),
 ((3, 4, 8), 0.5115164960684782),
 ((6, 8, 9), 0.5129217037789076),
 ((3, 6, 8), 0.5140772885882456),
 ((3, 4, 5, 6), 0.515554892641696),
 ((3, 4, 6, 8, 9), 0.5176087109095846),
 ((3, 4, 6, 8), 0.5183956480049541),
 ((3, 8, 9), 0.5187156177097489),
 ((3, 4, 8, 9), 0.5196011178567606),
 ((3, 6, 7), 0.5198778049286918),
 ((5,), 0.5218543806425342),
 ((7, 9), 0.5219400141140618),
 ((3, 4, 7, 9), 0.5225039555365436),
 ((3, 6, 8, 9), 0.523171543855319),
 ((3, 6, 7, 8), 0.5246426149541028),
 ((3, 7, 8), 0.5247239608431582),
 ((4, 7, 8), 0.5253809908315077),
 ((1, 4, 5, 6, 8), 0.5266054064534456),
 ((5, 8), 0.5275703573925083),
 ((1, 4, 6), 0.5288954354184696),
 ((3, 4, 5, 6, 8, 9), 0.5292060842610269),
 ((5, 7, 8), 0.5293956411632714),
 ((4, 5, 8), 0.5293967661706587),
 ((4, 5, 9), 0.5296518069402794),
 ((3, 4, 6, 7, 8, 9), 0.5302785508136112),
 ((5, 6, 9), 0.5302833083938312),
 ((4, 5, 6, 7, 8, 9), 0.5304145211574522),

# New Spurious Score

In [160]:
all_result_dict = read_all_result_file()
all_result_list = [
                    (
                        key,
                        all_result_dict[key]["ood_meta_dict"]["mean_indo_vacc"]*(abs(all_result_dict[key]["ood_meta_dict"]["mean_ood_drop"]))
                    ) 
                               for key in all_result_dict.keys()
                  ]
all_result_list.sort(key=lambda x:x[-1])
all_result_list[-1000:]

[((3, 4, 8, 9), 0.02619384597990937),
 ((6, 9), 0.026621433825521734),
 ((4, 7, 9), 0.026900771634026377),
 ((0, 4, 5), 0.027063104972116392),
 ((0, 2, 5, 8, 9), 0.027120668273606263),
 ((1, 3), 0.027146997658007432),
 ((0, 1, 4, 7, 9), 0.027153815578404128),
 ((0, 4, 6, 7, 9), 0.027202461291506275),
 ((0, 4, 7), 0.027379175533852163),
 ((0, 1, 3, 7, 9), 0.02754071736546937),
 ((0, 2, 7, 9), 0.02760372618008944),
 ((0, 3, 9), 0.02772604286186464),
 ((1, 9), 0.0277560441595599),
 ((0, 4, 5, 6), 0.027824543412807934),
 ((0, 1, 3, 7), 0.027933064919758888),
 ((0, 3, 4, 7, 9), 0.027936978037459426),
 ((3, 7, 9), 0.02796781118216707),
 ((1, 3, 4), 0.028014450086004672),
 ((4, 7), 0.028015950299387526),
 ((0, 1, 4, 7), 0.028090130156539495),
 ((0, 7), 0.028160215656489296),
 ((0, 5, 7), 0.028165176820154514),
 ((0, 1, 7, 9), 0.028282212065120937),
 ((7,), 0.02838220760251664),
 ((0, 5, 9), 0.028440495301634172),
 ((0, 2, 4, 5, 7, 9), 0.028444968108530366),
 ((0, 4, 9), 0.028623985721732303),

# Partition [causal,spurious] score

In [163]:
all_result_dict = read_all_result_file()
all_idx_set = set(range(10))
partition_score_list = []

for causal_idx,causal_result in all_result_dict.items():
    #Getting the other half of the partition
    spurious_idx = tuple(all_idx_set.difference(causal_idx))
    spurious_result = all_result_dict[spurious_idx]
    
    #Now we will get the overall score of this partition
#     causal_score = causal_result["ood_meta_dict"]["mean_indo_vacc"] * (1- abs(causal_result["ood_meta_dict"]["mean_ood_drop"]))
#     spurious_score = spurious_result["ood_meta_dict"]["mean_indo_vacc"] * (abs(spurious_result["ood_meta_dict"]["mean_ood_drop"]))
    
    causal_score =  (1- abs(causal_result["ood_meta_dict"]["mean_ood_drop"]))
    spurious_score = (abs(spurious_result["ood_meta_dict"]["mean_ood_drop"]))
    
    
    partition_score_list.append([causal_idx,spurious_idx,causal_score*spurious_score])

partition_score_list.sort(key=lambda x: x[-1])
partition_score_list[-1000:]
    

[[(1, 3, 6, 8), (0, 2, 4, 5, 7, 9), 0.04086141293968973],
 [(0, 1, 2, 3, 4, 5, 7, 8, 9), (6,), 0.04086393011235334],
 [(2, 3, 5, 6, 8, 9), (0, 1, 4, 7), 0.04118448489781712],
 [(1, 3, 8, 9), (0, 2, 4, 5, 6, 7), 0.04118478227485001],
 [(0, 2, 3, 4, 5, 6, 7, 8, 9), (1,), 0.041243505459137964],
 [(0, 1, 2, 3, 4, 5, 6, 8), (7, 9), 0.041270248744172844],
 [(3, 5, 6, 8), (0, 1, 2, 4, 7, 9), 0.04144340555877746],
 [(2, 4, 5, 6, 9), (0, 1, 3, 7, 8), 0.041612723991178324],
 [(0, 2, 3, 5, 6, 7, 8, 9), (1, 4), 0.041678848897057266],
 [(2, 3, 4, 6, 9), (0, 1, 5, 7, 8), 0.04171623075113588],
 [(1, 2, 3, 7, 8, 9), (0, 4, 5, 6), 0.041720486322046],
 [(3, 5, 7, 8, 9), (0, 1, 2, 4, 6), 0.04174504528045539],
 [(1, 2, 3, 4, 5, 6, 8, 9), (0, 7), 0.041766249205142575],
 [(1, 2, 3, 5, 6, 8), (0, 4, 7, 9), 0.041860855000446395],
 [(3, 4, 5, 8, 9), (0, 1, 2, 6, 7), 0.04187367796176261],
 [(0, 1, 2, 3, 5, 7, 8, 9), (4, 6), 0.042102896479342705],
 [(1, 2, 3, 4, 6, 8, 9), (0, 5, 7), 0.04226793478770996],
 [(1, 2

In [168]:
all_result_dict = read_all_result_file()
all_idx_set = set(range(10))
partition_score_list = []

for causal_idx,causal_result in all_result_dict.items():
    #Getting the other half of the partition
    spurious_idx = tuple(all_idx_set.difference(causal_idx))
    spurious_result = all_result_dict[spurious_idx]
    
    #Now we will get the overall score of this partition
    causal_score = causal_result["ood_meta_dict"]["mean_indo_vacc"] * (1- abs(causal_result["ood_meta_dict"]["mean_ood_drop"]))
    spurious_score = spurious_result["ood_meta_dict"]["mean_indo_vacc"] * (abs(spurious_result["ood_meta_dict"]["mean_ood_drop"]))
    
#     causal_score =  (1- abs(causal_result["ood_meta_dict"]["mean_ood_drop"]))
#     spurious_score = (abs(spurious_result["ood_meta_dict"]["mean_ood_drop"]))
    
    
    partition_score_list.append([causal_idx,spurious_idx,causal_score*spurious_score])

partition_score_list.sort(key=lambda x: x[-1])
partition_score_list[-1000:]
    

[[(1, 3, 4, 5, 6, 8), (0, 2, 7, 9), 0.015472585709392021],
 [(4, 6, 8), (0, 1, 2, 3, 5, 7, 9), 0.015577608659885212],
 [(1, 3, 6, 8), (0, 2, 4, 5, 7, 9), 0.015585886612037494],
 [(1, 3, 8, 9), (0, 2, 4, 5, 6, 7), 0.015726582903559945],
 [(5, 6, 8, 9), (0, 1, 2, 3, 4, 7), 0.015732002080211947],
 [(0, 1, 2, 4, 5, 6, 7, 8), (3, 9), 0.015779514570991835],
 [(1, 4, 7, 8), (0, 2, 3, 5, 6, 9), 0.015909720159804613],
 [(1, 2, 3, 5, 8), (0, 4, 6, 7, 9), 0.015919610218106638],
 [(3, 5, 7, 8, 9), (0, 1, 2, 4, 6), 0.015950722868927927],
 [(3, 8), (0, 1, 2, 4, 5, 6, 7, 9), 0.015950959720670302],
 [(2, 4, 5, 6, 8), (0, 1, 3, 7, 9), 0.01597310551705444],
 [(1, 2, 3, 6, 7, 8, 9), (0, 4, 5), 0.016303895462926567],
 [(1, 2, 3, 7, 8, 9), (0, 4, 5, 6), 0.016306270526278616],
 [(3, 4), (0, 1, 2, 5, 6, 7, 8, 9), 0.016376578110661552],
 [(1, 2, 4, 5, 6, 7, 8), (0, 3, 9), 0.016379823552440564],
 [(3, 5, 6, 8, 9), (0, 1, 2, 4, 7), 0.016408460501094835],
 [(1, 2, 3, 4, 6, 8, 9), (0, 5, 7), 0.01644711273362971],

In [193]:
all_result_dict = read_all_result_file()
all_idx_set = set(range(10))
partition_score_list = []

for causal_idx,causal_result in all_result_dict.items():
    #Getting the other half of the partition
    spurious_idx = tuple(all_idx_set.difference(causal_idx))
    spurious_result = all_result_dict[spurious_idx]
    
    #Now we will get the overall score of this partition
#     causal_score = causal_result["ood_meta_dict"]["mean_indo_vacc"] * (1- abs(causal_result["ood_meta_dict"]["mean_ood_drop"]))
#     spurious_score = spurious_result["ood_meta_dict"]["mean_indo_vacc"] * (abs(spurious_result["ood_meta_dict"]["mean_ood_drop"]))
    
#     causal_score =  (1- abs(causal_result["ood_meta_dict"]["mean_ood_drop"]))
#     spurious_score = (abs(spurious_result["ood_meta_dict"]["mean_ood_drop"]))

    causal_score    = causal_result["ood_meta_dict"]["mean_all_vacc"]
    spurious_score  = abs(spurious_result["ood_meta_dict"]["mean_ood_drop"])
    
    
    partition_score_list.append([causal_idx,spurious_idx,causal_score*spurious_score])

partition_score_list.sort(key=lambda x: x[-1])
partition_score_list[-1000:]
    

[[(1, 3, 6, 8), (0, 2, 4, 5, 7, 9), 0.02550293483848365],
 [(3, 5, 6, 8), (0, 1, 2, 4, 7, 9), 0.025565342124554746],
 [(4, 8, 9), (0, 1, 2, 3, 5, 6, 7), 0.02561358121616486],
 [(1, 4, 7, 8), (0, 2, 3, 5, 6, 9), 0.02562071863578952],
 [(1, 3, 8, 9), (0, 2, 4, 5, 6, 7), 0.025777204456503888],
 [(1, 2, 5, 6, 8, 9), (0, 3, 4, 7), 0.025806253803623003],
 [(3, 4, 6, 8), (0, 1, 2, 5, 7, 9), 0.025875414522907647],
 [(3, 5, 8, 9), (0, 1, 2, 4, 6, 7), 0.02602017600706441],
 [(3, 5, 8), (0, 1, 2, 4, 6, 7, 9), 0.026031812123300524],
 [(1, 2, 3, 5, 8), (0, 4, 6, 7, 9), 0.026092409069052636],
 [(3, 4, 5, 6, 7, 8, 9), (0, 1, 2), 0.026107182736246237],
 [(6, 7, 8, 9), (0, 1, 2, 3, 4, 5), 0.026125127674252457],
 [(3, 4, 5, 7, 8), (0, 1, 2, 6, 9), 0.026195996785862707],
 [(3, 4, 5, 6, 8, 9), (0, 1, 2, 7), 0.02625692866676843],
 [(2, 3, 4, 5, 6, 8), (0, 1, 7, 9), 0.026405034608516953],
 [(2, 4, 5, 6, 8, 9), (0, 1, 3, 7), 0.02647545420103392],
 [(3, 6, 8), (0, 1, 2, 4, 5, 7, 9), 0.02648945496639854],
 [(1

In [175]:
all_result_dict = read_all_result_file()
all_result_list = [
                    (
                        key,
                        all_result_dict[key]["ood_meta_dict"]["mean_indo_vacc"]*(1-abs(all_result_dict[key]["ood_meta_dict"]["mean_ood_drop"]))
                    ) 
                        for key in all_result_dict.keys() if len(key)==1
                ]
all_result_list.sort(key=lambda x:x[-1])
all_result_list

[((4,), 0.477614049768466),
 ((8,), 0.4846055840923498),
 ((9,), 0.48671293030787144),
 ((3,), 0.49036444243673927),
 ((6,), 0.4920127408837449),
 ((5,), 0.5218543806425342),
 ((1,), 0.5315305962219847),
 ((7,), 0.5611915333566508),
 ((0,), 0.5726875891060987),
 ((2,), 0.6050078645121655)]

# Three way partition [causal,spurious,unwanted]

In [199]:
from more_itertools import set_partitions
all_result_dict = read_all_result_file()
all_idx_set = list(range(10))
all_three_partitions = set_partitions(all_idx_set,k=3)
partition_score_list = []

for causal_idx,spurious_idx,useless_idx in all_three_partitions:
    #Getting the other half of the partition
    causal_result   = all_result_dict[tuple(causal_idx)]
    spurious_result = all_result_dict[tuple(spurious_idx)]
    useless_result  = all_result_dict[tuple(useless_idx)]
    
    #Now we will get the overall score of this partition
#     causal_score = causal_result["ood_meta_dict"]["mean_indo_vacc"] * (1- abs(causal_result["ood_meta_dict"]["mean_ood_drop"]))
#     spurious_score = spurious_result["ood_meta_dict"]["mean_indo_vacc"] * (abs(spurious_result["ood_meta_dict"]["mean_ood_drop"]))
    
#     causal_score =  (1- abs(causal_result["ood_meta_dict"]["mean_ood_drop"]))
#     spurious_score = (abs(spurious_result["ood_meta_dict"]["mean_ood_drop"]))

    causal_score    = causal_result["ood_meta_dict"]["mean_all_vacc"]          #large ood accuracy
    spurious_score  = abs(spurious_result["ood_meta_dict"]["mean_ood_drop"])   #large drops
    useless_score   = 1-useless_result["ood_meta_dict"]["mean_indo_vacc"]       #even indo acc is bad
    
    
    partition_score_list.append([tuple(causal_idx),tuple(spurious_idx),tuple(useless_idx),causal_score*spurious_score*useless_score])

partition_score_list.sort(key=lambda x: x[-1])
partition_score_list[-10:]
    

[[(0, 1, 2, 3, 4, 7), (5, 6, 8), (9,), 0.03208221559453751],
 [(0, 1, 2, 6), (5, 7, 8), (3, 4, 9), 0.03258019427385352],
 [(0, 1, 2, 4), (3, 5, 6, 8), (7, 9), 0.032713667408933424],
 [(0, 1, 2, 3), (4, 5, 6, 8), (7, 9), 0.03273483735559759],
 [(0, 1, 2, 3, 4, 6), (5, 7, 8), (9,), 0.03284655736660443],
 [(0, 1, 2, 3, 6), (5, 7, 8), (4, 9), 0.03306309482852771],
 [(0, 1, 2, 7), (4, 5, 6, 8), (3, 9), 0.03406883326774767],
 [(0, 1, 2, 3, 7), (4, 5, 6, 8), (9,), 0.03472483006866974],
 [(0, 1, 2, 7), (3, 5, 6, 8), (4, 9), 0.036243713472452636],
 [(0, 1, 2, 4, 7), (3, 5, 6, 8), (9,), 0.03644764735959215]]

In [208]:
from more_itertools import set_partitions
all_result_dict = read_all_result_file()
all_idx_set = list(range(10))
all_three_partitions = set_partitions(all_idx_set,k=3)
partition_score_list = []

for causal_idx,spurious_idx,useless_idx in all_three_partitions:
    #Getting the other half of the partition
    causal_result   = all_result_dict[tuple(causal_idx)]
    spurious_result = all_result_dict[tuple(spurious_idx)]
    useless_result  = all_result_dict[tuple(useless_idx)]
    
    #Now we will get the overall score of this partition
#     causal_score = causal_result["ood_meta_dict"]["mean_indo_vacc"] * (1- abs(causal_result["ood_meta_dict"]["mean_ood_drop"]))
#     spurious_score = spurious_result["ood_meta_dict"]["mean_indo_vacc"] * (abs(spurious_result["ood_meta_dict"]["mean_ood_drop"]))
    
#     causal_score =  (1- abs(causal_result["ood_meta_dict"]["mean_ood_drop"]))
#     spurious_score = (abs(spurious_result["ood_meta_dict"]["mean_ood_drop"]))

    causal_score    = 1-abs(causal_result["ood_meta_dict"]["mean_ood_drop"])         #low drop
    spurious_score  = abs(spurious_result["ood_meta_dict"]["mean_ood_drop"])         #large drops
    useless_score   = 1-useless_result["ood_meta_dict"]["mean_indo_vacc"]            #even indo acc is bad
    
    
    partition_score_list.append([tuple(causal_idx),tuple(spurious_idx),tuple(useless_idx),causal_score*spurious_score*useless_score])

partition_score_list.sort(key=lambda x: x[-1])
partition_score_list[-100:]
    

[[(1, 2, 7), (3, 5, 6, 8), (0, 4, 9), 0.0412958758291121],
 [(0, 1, 2, 3, 7), (5, 8), (4, 6, 9), 0.04130810972052006],
 [(0, 2, 6, 7), (3, 4, 5, 8), (1, 9), 0.041333911518891195],
 [(0, 1, 2, 3), (4, 5, 6, 7, 8), (9,), 0.04133645450940697],
 [(0, 2, 4, 6), (5, 7, 8), (1, 3, 9), 0.041345745683551795],
 [(0, 1, 2, 3), (5, 6, 7), (4, 8, 9), 0.0413636577700382],
 [(1, 2, 4, 7), (3, 5, 6, 8), (0, 9), 0.04136827160489023],
 [(0, 2, 3, 4, 6, 7), (1, 5, 8), (9,), 0.04139736162878466],
 [(0, 2, 3, 4, 7), (5, 6, 8), (1, 9), 0.04142257778791801],
 [(0, 2, 7), (1, 4, 5, 8), (3, 6, 9), 0.04156048405633666],
 [(0, 3, 7), (1, 2, 5, 6, 8), (4, 9), 0.041606084157741606],
 [(0, 1, 2), (3, 5, 7, 8), (4, 6, 9), 0.041635513726175556],
 [(0, 1, 3, 4, 7), (2, 5, 6, 8), (9,), 0.04166602322903813],
 [(0, 7), (1, 2, 3, 5, 6, 8), (4, 9), 0.04169696220896041],
 [(0, 1, 2, 4, 7), (5, 8), (3, 6, 9), 0.041704549669645825],
 [(0, 2, 3, 7), (1, 4, 5, 8), (6, 9), 0.04170496303658092],
 [(0, 2, 3, 6), (5, 7, 8), (1, 4, 

In [209]:
from more_itertools import set_partitions
all_result_dict = read_all_result_file()
all_idx_set = list(range(10))
all_three_partitions = set_partitions(all_idx_set,k=3)
partition_score_list = []

for causal_idx,spurious_idx,useless_idx in all_three_partitions:
    #Getting the other half of the partition
    causal_result   = all_result_dict[tuple(causal_idx)]
    spurious_result = all_result_dict[tuple(spurious_idx)]
    useless_result  = all_result_dict[tuple(useless_idx)]
    
    #Now we will get the overall score of this partition
#     causal_score = causal_result["ood_meta_dict"]["mean_indo_vacc"] * (1- abs(causal_result["ood_meta_dict"]["mean_ood_drop"]))
#     spurious_score = spurious_result["ood_meta_dict"]["mean_indo_vacc"] * (abs(spurious_result["ood_meta_dict"]["mean_ood_drop"]))
    
#     causal_score =  (1- abs(causal_result["ood_meta_dict"]["mean_ood_drop"]))
#     spurious_score = (abs(spurious_result["ood_meta_dict"]["mean_ood_drop"]))

    causal_score    = causal_result["ood_meta_dict"]["mean_all_vacc"]* ( 1-abs(causal_result["ood_meta_dict"]["mean_ood_drop"]) )        #low drop
    spurious_score  = spurious_result["ood_meta_dict"]["mean_all_vacc"]* abs(spurious_result["ood_meta_dict"]["mean_ood_drop"])         #large drops
    useless_score   = 1-useless_result["ood_meta_dict"]["mean_indo_vacc"]            #even indo acc is bad
    
    
    partition_score_list.append([tuple(causal_idx),tuple(spurious_idx),tuple(useless_idx),causal_score*spurious_score*useless_score])

partition_score_list.sort(key=lambda x: x[-1])
partition_score_list[-100:]
    

[[(0, 2, 7), (1, 4, 5, 8), (3, 6, 9), 0.014843997711124978],
 [(0, 4, 7), (1, 2, 3, 5, 6, 8), (9,), 0.01487613519858359],
 [(0, 1, 2, 6, 7), (5, 8), (3, 4, 9), 0.01487973366057789],
 [(0, 2, 4), (1, 3, 5, 6, 7), (8, 9), 0.014889959462548858],
 [(0, 1, 6, 7), (2, 3, 4, 5, 8), (9,), 0.014894799772362431],
 [(0, 2), (1, 3, 4, 5, 6, 7), (8, 9), 0.01490506885013663],
 [(0, 2), (1, 4, 5, 6, 7), (3, 8, 9), 0.014906641046469896],
 [(0, 2, 7), (4, 5, 6, 8), (1, 3, 9), 0.014971105794155367],
 [(0, 1, 3), (2, 4, 5, 6, 8), (7, 9), 0.014976373533354058],
 [(0, 1, 2, 3, 4, 6, 7), (5, 8), (9,), 0.01497849602430448],
 [(0, 1, 2, 5), (3, 4, 6, 7, 8), (9,), 0.014978501816452227],
 [(0, 1, 2), (5, 6, 8), (3, 4, 7, 9), 0.01501409534543174],
 [(0, 1, 2), (5, 6, 7), (3, 4, 8, 9), 0.015020081264918248],
 [(0, 2, 6, 7), (1, 4, 5, 8), (3, 9), 0.015021994253256593],
 [(0, 1, 2, 4, 6, 7), (5, 8), (3, 9), 0.015028176919592285],
 [(0, 1, 4, 7), (2, 5, 6, 8), (3, 9), 0.015054533181033782],
 [(0, 2, 3, 7), (1, 4, 5,

In [45]:
from more_itertools import set_partitions
all_result_dict = read_all_result_file()
all_idx_set = list(range(10))
all_three_partitions = set_partitions(all_idx_set,k=3)
partition_score_list = []

for causal_idx,spurious_idx,useless_idx in all_three_partitions:
    #Getting the other half of the partition
    causal_result   = all_result_dict[tuple(causal_idx)]
    spurious_result = all_result_dict[tuple(spurious_idx)]
    useless_result  = all_result_dict[tuple(useless_idx)]
    
    #Now we will get the overall score of this partition
#     causal_score = causal_result["ood_meta_dict"]["mean_indo_vacc"] * (1- abs(causal_result["ood_meta_dict"]["mean_ood_drop"]))
#     spurious_score = spurious_result["ood_meta_dict"]["mean_indo_vacc"] * (abs(spurious_result["ood_meta_dict"]["mean_ood_drop"]))
    
#     causal_score =  (1- abs(causal_result["ood_meta_dict"]["mean_ood_drop"]))
#     spurious_score = (abs(spurious_result["ood_meta_dict"]["mean_ood_drop"]))

    causal_score    = causal_result["ood_meta_dict"]["mean_indo_vacc"]               #large indomain performance
    spurious_score  = spurious_result["ood_meta_dict"]["irm_score"]                 #large avg classifier wrongness
    useless_score   = 1-useless_result["ood_meta_dict"]["mean_indo_vacc"]            #even indo acc is bad
    
    overall_score = causal_score * spurious_score * useless_score
    
    
    partition_score_list.append([tuple(causal_idx),tuple(spurious_idx),tuple(useless_idx),overall_score])

partition_score_list.sort(key=lambda x: x[-1])
partition_score_list[-100:]
    

Getting spurousness score for:[1, 3, 5, 7, 9]
Perf Better than optimal perf:	curr:arts	other:clothes	drop:0.01843315362930298
Perf Better than optimal perf:	curr:books	other:arts	drop:0.01612907648086548
Perf Better than optimal perf:	curr:books	other:phones	drop:0.01612907648086548
Perf Better than optimal perf:	curr:books	other:groceries	drop:0.01612907648086548
Perf Better than optimal perf:	curr:books	other:tools	drop:0.023041486740112305
Perf Better than optimal perf:	curr:groceries	other:tools	drop:0.0023041963577270508
Perf Better than optimal perf:	curr:movies	other:books	drop:0.02534562349319458
Perf Better than optimal perf:	curr:pets	other:arts	drop:0.02534562349319458
Perf Better than optimal perf:	curr:pets	other:phones	drop:0.02534562349319458
Perf Better than optimal perf:	curr:pets	other:groceries	drop:0.02534562349319458
Perf Better than optimal perf:	curr:pets	other:tools	drop:0.023041486740112305
Getting spurousness score for:[0, 1, 2, 3, 6, 7]
Perf Better than optim

Getting spurousness score for:[0, 2, 4, 5, 6, 9]
Perf Better than optimal perf:	curr:arts	other:phones	drop:0.02995389699935913
Perf Better than optimal perf:	curr:arts	other:groceries	drop:0.027649760246276855
Perf Better than optimal perf:	curr:arts	other:pets	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:tools	drop:0.027649760246276855
Perf Better than optimal perf:	curr:books	other:arts	drop:0.05529952049255371
Perf Better than optimal perf:	curr:books	other:phones	drop:0.009216606616973877
Perf Better than optimal perf:	curr:books	other:groceries	drop:0.05990785360336304
Perf Better than optimal perf:	curr:books	other:movies	drop:0.03917050361633301
Perf Better than optimal perf:	curr:books	other:pets	drop:0.027649760246276855
Perf Better than optimal perf:	curr:books	other:tools	drop:0.05069124698638916
Perf Better than optimal perf:	curr:phones	other:arts	drop:0.020737290382385254
Perf Better than optimal perf:	curr:phones	other:books	drop:0.018433153

Perf Better than optimal perf:	curr:pets	other:movies	drop:0.0069124698638916016
Perf Better than optimal perf:	curr:tools	other:books	drop:0.02764981985092163
Perf Better than optimal perf:	curr:tools	other:phones	drop:0.0069124698638916016
Perf Better than optimal perf:	curr:tools	other:movies	drop:0.011520743370056152
Perf Better than optimal perf:	curr:tools	other:pets	drop:0.02764981985092163
Getting spurousness score for:[0, 1, 2, 4, 6, 9]
Perf Better than optimal perf:	curr:arts	other:books	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:groceries	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:movies	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:pets	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:phones	other:arts	drop:0.03917050361633301
Perf Better than optimal perf:	curr:phones	other:books	drop:0.023041486740112305
Perf Better than optimal perf:	curr:phones	other:clothes	drop:0.00

Getting spurousness score for:[2, 4, 5, 6, 7, 8, 9]
Perf Better than optimal perf:	curr:books	other:arts	drop:0.05069124698638916
Perf Better than optimal perf:	curr:books	other:phones	drop:0.02534562349319458
Perf Better than optimal perf:	curr:books	other:groceries	drop:0.055299580097198486
Perf Better than optimal perf:	curr:books	other:movies	drop:0.04147469997406006
Perf Better than optimal perf:	curr:books	other:pets	drop:0.052995383739471436
Perf Better than optimal perf:	curr:phones	other:arts	drop:0.043778836727142334
Perf Better than optimal perf:	curr:phones	other:clothes	drop:0.013824880123138428
Perf Better than optimal perf:	curr:phones	other:groceries	drop:0.043778836727142334
Perf Better than optimal perf:	curr:phones	other:movies	drop:0.004608273506164551
Perf Better than optimal perf:	curr:phones	other:pets	drop:0.02995389699935913
Perf Better than optimal perf:	curr:groceries	other:movies	drop:0.009216547012329102
Perf Better than optimal perf:	curr:groceries	other:p

Perf Better than optimal perf:	curr:movies	other:pets	drop:0.020737290382385254
Perf Better than optimal perf:	curr:movies	other:tools	drop:0.03917050361633301
Perf Better than optimal perf:	curr:pets	other:arts	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:pets	other:clothes	drop:0.0069124698638916016
Getting spurousness score for:[0, 2, 3, 4, 5, 8, 9]
Perf Better than optimal perf:	curr:arts	other:phones	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:movies	drop:0.0069124698638916016
Perf Better than optimal perf:	curr:arts	other:tools	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:books	other:arts	drop:0.023041486740112305
Perf Better than optimal perf:	curr:books	other:phones	drop:0.02534562349319458
Perf Better than optimal perf:	curr:books	other:groceries	drop:0.057603657245635986
Perf Better than optimal perf:	curr:books	other:movies	drop:0.07603687047958374
Perf Better than optimal perf:	curr:books	other:pets	drop:0.02

...

Perf Better than optimal perf:	curr:groceries	other:pets	drop:0.004608273506164551
Perf Better than optimal perf:	curr:movies	other:arts	drop:0.01843315362930298
Perf Better than optimal perf:	curr:movies	other:groceries	drop:0.016129016876220703
Perf Better than optimal perf:	curr:movies	other:pets	drop:0.01843315362930298
Perf Better than optimal perf:	curr:pets	other:phones	drop:0.023041486740112305
Perf Better than optimal perf:	curr:pets	other:movies	drop:0.016129016876220703
Perf Better than optimal perf:	curr:tools	other:arts	drop:0.05760371685028076
Perf Better than optimal perf:	curr:tools	other:books	drop:0.023041486740112305
Perf Better than optimal perf:	curr:tools	other:phones	drop:0.03225809335708618
Perf Better than optimal perf:	curr:tools	other:clothes	drop:0.0023041963577270508
Perf Better than optimal perf:	curr:tools	other:groceries	drop:0.052995383739471436
Perf Better than optimal perf:	curr:tools	other:movies	drop:0.052995383739471436
Perf Better than optimal per

Getting spurousness score for:[0, 1, 3, 4]
Perf Better than optimal perf:	curr:arts	other:phones	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:arts	other:pets	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:clothes	other:arts	drop:0.004608273506164551
Perf Better than optimal perf:	curr:clothes	other:phones	drop:0.006912410259246826
Perf Better than optimal perf:	curr:clothes	other:pets	drop:0.006912410259246826
Perf Better than optimal perf:	curr:clothes	other:tools	drop:0.004608273506164551
Perf Better than optimal perf:	curr:groceries	other:arts	drop:0.048387110233306885
Perf Better than optimal perf:	curr:groceries	other:phones	drop:0.08294934034347534
Perf Better than optimal perf:	curr:groceries	other:clothes	drop:0.07373273372650146
Perf Better than optimal perf:	curr:groceries	other:pets	drop:0.08294934034347534
Perf Better than optimal perf:	curr:groceries	other:tools	drop:0.048387110233306885
Perf Better than optimal perf:	curr:movies	other:boo

Getting spurousness score for:[0, 1, 2, 3, 7, 8, 9]
Perf Better than optimal perf:	curr:arts	other:phones	drop:0.009216606616973877
Perf Better than optimal perf:	curr:arts	other:groceries	drop:0.011520743370056152
Perf Better than optimal perf:	curr:arts	other:pets	drop:0.013824939727783203
Perf Better than optimal perf:	curr:arts	other:tools	drop:0.011520743370056152
Perf Better than optimal perf:	curr:books	other:groceries	drop:0.004608273506164551
Perf Better than optimal perf:	curr:books	other:tools	drop:0.009216606616973877
Perf Better than optimal perf:	curr:phones	other:books	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:clothes	other:arts	drop:0.08525341749191284
Perf Better than optimal perf:	curr:clothes	other:books	drop:0.02304142713546753
Perf Better than optimal perf:	curr:clothes	other:phones	drop:0.07373267412185669
Perf Better than optimal perf:	curr:clothes	other:groceries	drop:0.07373267412185669
Perf Better than optimal perf:	curr:clothes	other:movi

Getting spurousness score for:[0, 1, 2, 4, 5, 6, 7]
Perf Better than optimal perf:	curr:arts	other:movies	drop:0.0023041367530822754
Perf Better than optimal perf:	curr:phones	other:arts	drop:0.023041486740112305
Perf Better than optimal perf:	curr:phones	other:books	drop:0.05299544334411621
Perf Better than optimal perf:	curr:phones	other:groceries	drop:0.05069124698638916
Perf Better than optimal perf:	curr:phones	other:movies	drop:0.03225809335708618
Perf Better than optimal perf:	curr:phones	other:pets	drop:0.03456223011016846
Perf Better than optimal perf:	curr:phones	other:tools	drop:0.02534562349319458
Perf Better than optimal perf:	curr:movies	other:books	drop:0.04147469997406006
Perf Better than optimal perf:	curr:movies	other:groceries	drop:0.03456223011016846
Perf Better than optimal perf:	curr:pets	other:tools	drop:0.006912410259246826
Perf Better than optimal perf:	curr:tools	other:arts	drop:0.004608273506164551
Perf Better than optimal perf:	curr:tools	other:movies	drop:0

[[(0, 2, 7), (1, 3, 5, 6, 8), (4, 9), 0.018887146488086662],
 [(0, 1, 3, 4), (2, 5, 6, 7), (8, 9), 0.018896260108153387],
 [(0, 1, 2, 3, 6), (4, 5, 8), (7, 9), 0.018928856614740565],
 [(0,), (1, 2, 3, 5, 6), (4, 7, 8, 9), 0.01898751675624837],
 [(0, 2, 3, 4), (5, 6, 8), (1, 7, 9), 0.019005112468419065],
 [(0, 2, 4, 7), (1, 3, 5, 6, 8), (9,), 0.019015930185072995],
 [(0, 2, 3), (5, 6, 8), (1, 4, 7, 9), 0.01906368455543544],
 [(0, 1, 2, 6), (5, 7, 8), (3, 4, 9), 0.01906828257005823],
 [(0, 2, 3, 4, 6, 7), (5, 8), (1, 9), 0.019069451015369606],
 [(0, 3), (1, 2, 4, 5), (6, 7, 8, 9), 0.019079919946661025],
 [(0, 2, 6, 7), (1, 5, 8), (3, 4, 9), 0.019092724269552913],
 [(0, 2, 4, 6, 7), (1, 5, 8), (3, 9), 0.01909552136998777],
 [(0, 2, 4), (5, 6, 8), (1, 3, 7, 9), 0.019095629163033517],
 [(0, 1, 2, 7), (3, 4, 5, 8), (6, 9), 0.01910255172659074],
 [(0, 1, 2, 3, 4), (5, 8), (6, 7, 9), 0.019111819261116516],
 [(0, 1, 3, 4, 7), (2, 5, 6, 8), (9,), 0.019116077265979702],
 [(0, 1, 2, 3, 6), (5, 8),